In [1]:
import numpy as np
import pandas as pd
import random
from random import *
from keras.models import Sequential
from keras.layers import Dense, Dropout, BatchNormalization
from keras.optimizers import Adam, RMSprop
from keras.models import load_model

from collections import deque

In [2]:
model = load_model("model.h5")

types = ['6633', '6024', '1062', '6310', '6128', '6287', '1075', '1076',
       '6756', '6757', '1101', '6494', '6662', '6705', '6549', '6552',
       '6527', '6531', '1099', '1104', '6754', '6575', '6706', '6589',
       '6232', '6752', '6574', '6053', 'P828', '6692', '6721', '6663',
       '6734', '6681', '6682', '6561', '6750', '6728', '6648', '6584',
       '6102', '6630', '6406', '6407', '1106', '1107', '6542', '6723',
       '6356', '6700', '6572', '6573', '6218', '1017', 'P130', '6763',
       '6650', '6653', '6454', '6452', '6696', '8L39', '8L72', '6698',
       '6433', '6629', '6760', '6380', 'P099', '6585', '6581', '6447',
       '6689', '6761', '6040', '6515', '6217', '6747', '6769', '6738',
       '6751', '6112', '6753', '6301', '6271', '6432', '6675', '6470',
       '6647', '1018', '6238', '6324', '6733', '6206', 'P163', '6719',
       '6205', '6660', '6453', '6655', '6646', '6244', '6695', '6539',
       '6736', '6683', '6634', '6475', 'P147', '6642', '6684', '6477',
       '6608', '6708', 'P837', 'P820', 'P835', '8K52']
machine = [[],[],[],[],[],[],[],[],[],[],[],[],[],[],[],[]]
machine_state = [[1,0],[1,0],[1,0],[1,0],[1,0],[1,0],[1,0],[1,0],[1,0],[1,0],[1,0],[1,0],[1,0],[1,0],[1,0],[1,0]]

df = pd.read_csv("C:\\Users\\wg999\\OneDrive\\바탕 화면\\data_scheduling.csv")

In [3]:
new_table = pd.read_csv("C:\\Users\\wg999\\OneDrive\\바탕 화면\\data_const.csv")

new_table01 = new_table.groupby('machine').agg(lambda x: ','.join(set(x)))
new_table01 = new_table01.reset_index()
new_table01 = new_table01.reset_index()
del new_table01['machine']
new_table01.columns = ['machine','type']
new_table01
for i in range(0,16):
    new_table01['type'][i] = new_table01['type'][i].split(',') 
new_table01

<ipython-input-3-682eae0fad33>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_table01['type'][i] = new_table01['type'][i].split(',')


machine                                               type
0         0  [6454, 6552, 6324, 6630, 6634, 6662, 6112, 110...
1         1  [6454, 6552, 6646, 6630, 6634, 6662, 6356, 110...
2         2  [6454, 6552, 6630, 6662, 6112, 1106, 6754, P13...
3         3  [P828, 6475, 6040, 6769, 6736, P147, 6301, 627...
4         4  [6454, 6552, 6646, 6630, 6634, 6662, 1106, 675...
5         5  [6629, 6585, 6432, 1075, 6662, 6752, 6754, 675...
6         6  [6454, 6552, 6630, 6662, 6112, 1106, 6754, P13...
7         7  [6454, 6552, 6630, 6634, 6662, 6112, 1106, 675...
8         8  [6454, 6552, 6646, 6630, 6634, 6662, 1106, 675...
9         9  [P828, 6475, 6040, 6218, 6769, 6736, 6581, P14...
10       10  [P828, 6475, 6040, 1017, 6754, 6750, 6769, 672...
11       11  [6549, 6575, 6719, 6634, 6470, 6728, 6218, 663...
12       12  [6454, 6552, 6630, 6662, 6112, 1106, 6754, P13...
13       13  [6454, 6552, 6646, 6630, 6662, 1106, 6754, 669...
14       14  [6454, 6552, 6646, 6630, 6634, 6662, 1106, 675...
15       15  [6454, 6552, 6646, 6630, 6634, 6662, 1106, 675...

In [4]:
job_change_count = 0
validation_date_count = 0
done = False

current_type = df['type'][0]
current_process_time = df['process_time'][0]
current_due_date = df['due_date'][0]

for j in range(len(machine_state)):
    if len(machine[j]) == 0 or machine[j][-1] == current_type:
        machine_state[j][0] = 1
    
    else:
        machine_state[j][0] = 0

for j in range(len(machine_state)):
    machine_state[j][1] = current_due_date - (len(machine[j]) + current_process_time)

machine_state_np = np.array(machine_state)
machine_state_flatten = machine_state_np.flatten()
machine_state_final = machine_state_flatten.tolist()

state = np.array(machine_state_final)

state = state.reshape(1, 32)

for i in range(1, len(df)):
    
    if i == len(df)-2:
        done = True
    #action
    #-----------------------------------------------------------
    blank = []
    for j in range(len(new_table01['type'])):
        for k in range(len(new_table01['type'][j])):
            if new_table01['type'][j][k] == current_type:
                blank.append(j)
    score = model.predict(state)
    
    blank2 = []
    for j in blank:
        ax = score[0][j]
        blank2.append(ax)
    max_q_val = max(blank2)
    
    index_of_max = np.where(score[0] == max_q_val)
    iom = index_of_max[0][0]
    action = iom
    
    
    #-----------------------------------------------------------
    
    
    validation_due_date = 0
    job_change = 0
    
    if len(machine[action]) == 0 or machine[action][-1] == current_type:
        job_change = 0
    else:
        job_change = 1
        job_change_count +=1
    
    if machine_state[action][1] < 0:
        validation_due_date = -1 * machine_state[action][1]
        validation_date_count += validation_due_date
        
    for j in range(current_process_time):
            machine[action].append(current_type)
    
    for p in range(16):
        print(machine[p])
        
    print("-----------------------------------------------------------------")
    current_type = df['type'][i]
    current_process_time = df['process_time'][i]
    current_due_date = df['due_date'][i]
    
    for j in range(len(machine_state)):
        if len(machine[j]) == 0 or machine[j][-1] == current_type:
            machine_state[j][0] = 1
        else:
            machine_state[j][0] = 0
            
    for j in range(len(machine_state)):
        machine_state[j][1] = current_due_date - (len(machine[j]) + current_process_time)
        
    machine_state_np = np.array(machine_state)
    machine_state_flatten = machine_state_np.flatten()
    machine_state_final = machine_state_flatten.tolist()
    next_state = np.array(machine_state_final)
    next_state = next_state.reshape(1,32)
    
    
    state = next_state
    
for p in range(16):
    print(machine[p])
print("data_scheduling.csv : job_change_count = " + str(job_change_count) + ", validation_date_count = " + str(validation_date_count))

[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633']
[]
-----------------------------------------------------------------
[]
[]
[]
['6024', '6024', '6024', '6024', '6024', '6024']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633']
[]
-----------------------------------------------------------------
[]
[]
[]
['6024', '6024', '6024', '6024', '6024', '6024', '1062', '1062', '1062']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633']
[]
-----------------------------------------------------------------
[]
[]
[]
['6024', '6024', '6024', '6024', '6024', '6024', '1062', '1062', '1062']
[]
[]
['6310', '6310']
[]
[]
[]
[]
[]
[]
[]
['6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633', '6633']
[]
-----------------------------------------------------------------
[]
[]
[]
['6024', '6024', '6024'

['1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101']
[]
[]
['6024', '6024', '6024', '6024', '6024', '6024', '1062', '1062', '1062']
[]
['6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662']
['6310', '6310', '6310', '6310', '6310', '6310', '6310', '6128', '6128', '6128', '6128', '6128', '6128', '6128', '1076', '1076', '1076']
['6287', '6287', '6287', '6287', '6287', '6287', '6287', '6287', '6287', '6287']
[]
['6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549', '6549']
[]
['6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705', '6705']
['1075', '1075', '1075', '1075', '1075', '1075', '6756', '6756', '6756', '6756', '6756', '6756', '6756']
['6494', '6494', '6494', '6494', '6494', 

['1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101']
['1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104']
['6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527']
['6024', '6024', '6024', '6024', '6024', '6024', '1062', '1062', '1062']
['6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552']
['6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662']
['6310', '6310', '6310', '6310', '6310', '6310', '6310', '6128', '6128', '6128', '6128', '6128', '6128', '6128', '1076', '1076', '1076']
['6287', '6287', '6287', '6287', '6287', '6287', '6287', '6287', '6287', '6287']


['1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101']
['1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104']
['6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527']
['6024', '6024', '6024', '6024', '6024', '6024', '1062', '1062', '1062']
['6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552', '6552']
['6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6662', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754', '6754']
['6310', '6310', '6310', '6310', '6310', '6310', '6310', '

['1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589']
['1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104', '1104']
['6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6527', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053', '6053']
['6024', '6024', '6024', '6024', '6024', '6024', '1062', '1062', '1062', '6232', '6232', '6232', '6232', '6232', '6232', '6232', '6232', '623

...

['1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6452', '6452', '6452', '6452', '6452', '6452', '6452', '6452',

['1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6452', '6452', '6452', '6452', '6452', '6452', '6452', '6452',

['1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6452', '6452', '6452', '6452', '6452', '6452', '6452', '6452',

['1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6452', '6452', '6452', '6452', '6452', '6452', '6452', '6452',

['1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '1101', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6589', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6734', '6452', '6452', '6452', '6452', '6452', '6452', '6452', '6452',